In [6]:
import numpy as np
import pandas as pd 
import os
import matplotlib.pyplot as plt
import seaborn as sns
import sklearn
from itertools import product
import time
!pip install kmodes
from kmodes.kmodes import KModes

df = pd.read_csv('DATA/Truck_drivers_final.csv')

In [9]:
start_time = time.time()

from itertools import combinations
from sklearn import preprocessing
from kmodes.kmodes import KModes
# List of variable names
variables_name =   ['deviation', 'seniority_in_the_job_months', 'age', 'Quarter', 'time_workday', 'specific_physical_activity', 'injured_body_part', 'injury_description']


# Generate combinations of 4 to 8 variables
combinations_list = []
for r in range(5, 6):
    combinations_list.extend(combinations(variables_name, r))

# Empty DataFrame to store results
table = pd.DataFrame()

def tuple_to_list(t):
    new_list = []
    for element in t:
        new_list.append(element)
    return new_list

# Iterate over combinations
for selected_columns in combinations_list:
    # Select columns from 'variables' DataFrame based on the combination
    listavar = tuple_to_list(selected_columns)
    subgrup_1 = df[listavar]
    print(subgrup_1.shape[1])
    # Clustering code
    subgroup = subgrup_1.copy()
    from sklearn import preprocessing  
    le = preprocessing.LabelEncoder()
    subgroup_encoded = subgroup.apply(le.fit_transform)
    #to create the list to get the percenge of significant clusters
    l=[]
    # Iterate through cluster numbers
    for n_clusters in range(8, 16):
        # Clustering
        km = KModes(n_clusters=n_clusters, init='Cao', n_init=1, verbose=1)
        clusters = km.fit_predict(subgroup_encoded)

        # Combine with original data
        combined = pd.concat([subgroup.reset_index(), pd.DataFrame({'Cluster': clusters})], axis=1).drop('index', axis=1)

        # Create table
        table = pd.DataFrame(columns=range(n_clusters))

        # Fill in table with percentage of instances of each value in each cluster for each variable
        for var in subgroup.columns:
            by_cluster_value = combined.groupby(['Cluster', var]).size()
            percentages = by_cluster_value.groupby(level=0).apply(lambda x: x / x.sum() * 100)
            pivot_table = pd.pivot_table(percentages.reset_index(), index=var, columns='Cluster', values=0, fill_value=0)

            # Fill in table with percentage of instances for each value in each cluster
            for i, col in enumerate(pivot_table.columns):
                values = pivot_table[col].index.tolist()
                pct_values = pivot_table[col].tolist()
                for j, value in enumerate(values):
                    table.loc[value, i] = pct_values[j]
            # Add new column with variable names based on index
        table['VARIABLE'] = ''

        variable_mapping = {}

        for column in subgroup.columns:
            unique_values = subgroup[column].unique()
            variable_mapping[column] = unique_values

        for i, index_value in enumerate(table.index.values):
            for variable, values in variable_mapping.items():
                if index_value in values:
                    table.iloc[i, -1] = variable
                    break
        print(table)
        table = table.reset_index().rename(columns={'index': 'value'})
        table = table[['VARIABLE'] + list(table.columns[:-1])]
        #print(table)
        table = table.set_index('VARIABLE')       

        # Add a new row for the cluster drivers percentage
        table.loc['Cluster percentage of accidents'] = 0
        # Calculate the number of instances in each cluster
        cluster_counts = combined['Cluster'].value_counts()

        # Fill in the table with the percentage of instances in each cluster
        for i, count in cluster_counts.items():
            table.loc['Cluster percentage of accidents', i] = count / len(combined) * 100            
        #table.to_excel(f'table_{n_clusters}_clusters_pas1.xlsx', index=True)
        table1=table
        # Save table to CSV file
        table = table.drop('value', axis=1)
        new_table_2 = pd.DataFrame(index=table.index.unique())
    # Iterate over each column (0, 1, 2, 3) and find the highest percentage for each variable
        for col in table.columns:
            col_max = table.groupby(level=0)[col].max()
            new_table_2[col] = col_max
    # Add the 'Cluster percentage of accidents' row back to the new DataFrame
        new_table_2.loc['Cluster percentage of accidents'] = table.loc['Cluster percentage of accidents']
    # Display the new DataFrame
        #print(new_table_2)
        #new_table_2.to_excel(f'table_{n_clusters}_clusters_pas2.xlsx', index=True)
        new_table_3= new_table_2.loc[new_table_2.index != 'Cluster percentage of accidents'] = (new_table_2.loc[new_table_2.index != 'Cluster percentage of accidents'] >= 70).astype(int)
        new_table_3.loc['VARIABLES => 75%'] = new_table_3.sum()
        #new_table_2.to_excel(f'table_{n_clusters}_clusters_pas3.xlsx', index=True)
        #print(new_table_3)
        print(subgrup_1.shape[1])
        new_table_3.loc['Cluster Value'] = new_table_3 .loc['VARIABLES => 75%'] / subgrup_1.shape[1]
        new_table_3.loc['Cluster adequate?'] = new_table_3 .loc['Cluster Value']>0.5
        new_table_4=new_table_3
        new_table_4.loc['Cluster percentage of accidents'] = table.loc['Cluster percentage of accidents']
        new_table_4.loc['SCORE'] = np.nan
        new_table_4.loc['SCORE' ,'TOTAL CLUSTERIZATION VALUE'] = new_table_4.loc['Cluster adequate?'].sum() / n_clusters

        if new_table_4.loc['Cluster adequate?'].sum() / n_clusters > 0.60:
            table1.to_excel(f'table_{n_clusters}_clusters_{"".join(selected_columns)}.xlsx', index=True)

end_time = time.time()

# Calculate the elapsed time
elapsed_time = end_time - start_time
print("Elapsed Time:", elapsed_time, "seconds")

5
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run 1, iteration: 1/100, moves: 0, cost: 404769.0


<ipython-input-9-5c019188375e>:72: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                           0         1  \
Breakage, bursting, slipping, falling, collapsi...   6.36417   5.44957   
Electrical problem, explosion, fire                 0.406293  0.403961   
Falling persons – Slip or trip and fall              16.7815   46.1324   
Loss of total or partial control of work equipm...   13.0079   12.9737   
Movement of the body as a result of or with phy...   42.7306   12.1293   
Movement of the body without added physical effort   14.2836   16.2836   
Other deviations                                     3.62901   4.13604   
Overflow, overturning, leak, spill, emanation        1.78606   1.35262   
Surprise, fear, violence, aggression, threat, p...   1.01086   1.13891   
Experienced                                          14.3373   49.5517   
Junior employees                                     12.4553    12.369   
New hires                                            56.5901   15.3062   
Veterans                              

<ipython-input-9-5c019188375e>:72: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                           0         1  \
Breakage, bursting, slipping, falling, collapsi...   6.64544   5.60652   
Electrical problem, explosion, fire                 0.426244  0.420347   
Falling persons – Slip or trip and fall              17.8573   48.2093   
Loss of total or partial control of work equipm...   14.3952    13.667   
Movement of the body as a result of or with phy...   39.3745   7.59465   
Movement of the body without added physical effort   14.5642   17.7455   
Other deviations                                     3.79483   4.23755   
Overflow, overturning, leak, spill, emanation        1.89741   1.36897   
Surprise, fear, violence, aggression, threat, p...   1.04493   1.15027   
Experienced                                          10.3414   47.4623   
Junior employees                                     13.7837   12.7695   
New hires                                            59.1885   16.6804   
Veterans                              

...

<ipython-input-9-5c019188375e>:72: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                            0          1  \
1                                                     13.8563    50.8493   
2                                                     19.6228    17.6928   
3                                                     54.9607    17.3414   
4                                                     11.5602    14.1165   
Recently started working                              15.4476    67.0778   
Worked between 3 to 6 hours                           72.9356    17.0062   
Worked more than 6 hours                              11.6168     15.916   
Being present                                         1.86549    2.72372   
Driving/being on board a means of transport or ...    12.8522     18.233   
Machine operations                                     2.2939    2.94826   
Manual transportation                                 10.5402    9.51839   
Movement                                              62.4952    8.83176   
Object manip

<ipython-input-9-5c019188375e>:72: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


                                                            0          1  \
1                                                     13.5797    51.0921   
2                                                      19.972    17.2999   
3                                                     56.0811    17.4241   
4                                                     10.3672    14.1839   
Recently started working                              15.8876    66.9206   
Worked between 3 to 6 hours                           72.1646    17.0874   
Worked more than 6 hours                              11.9478     15.992   
Being present                                         1.90465    2.73673   
Driving/being on board a means of transport or ...    13.2183      18.32   
Machine operations                                    2.33127    2.96233   
Manual transportation                                 10.8404    9.56382   
Movement                                              61.5363    8.39655   
Object manip

<ipython-input-9-5c019188375e>:72: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if index_value in values:


In [8]:
new_table_4

0          1         2         3  \
VARIABLE                                                                    
Quarter                           0.000000   0.000000  0.000000  0.000000   
time_workday                      1.000000   0.000000  1.000000  1.000000   
specific_physical_activity        0.000000   0.000000  0.000000  0.000000   
injured_body_part                 1.000000   0.000000  0.000000  0.000000   
injury_description                1.000000   0.000000  0.000000  1.000000   
VARIABLES => 75%                  3.000000   0.000000  1.000000  2.000000   
Cluster Value                     0.600000   0.000000  0.200000  0.400000   
Cluster adequate?                 1.000000   0.000000  0.000000  0.000000   
Cluster percentage of accidents  20.278795  14.094741  9.367485  7.251549   
SCORE                                  NaN        NaN       NaN       NaN   

                                        4         5         6         7  \
VARIABLE                                                                  
Quarter                          1.000000  1.000000  0.000000  1.000000   
time_workday                     1.000000  1.000000  1.000000  1.000000   
specific_physical_activity       0.000000  0.000000  0.000000  0.000000   
injured_body_part                1.000000  1.000000  0.000000  1.000000   
injury_description               0.000000  0.000000  0.000000  1.000000   
VARIABLES => 75%                 3.000000  3.000000  1.000000  4.000000   
Cluster Value                    0.600000  0.600000  0.200000  0.800000   
Cluster adequate?                1.000000  1.000000  0.000000  1.000000   
Cluster percentage of accidents  5.945116  7.087279  7.028575  4.370394   
SCORE                                 NaN       NaN       NaN       NaN   

                                        8         9        10       11  \
VARIABLE                                                                 
Quarter                          1.000000  1.000000  1.000000  1.00000   
time_workday                     1.000000  1.000000  1.000000  1.00000   
specific_physical_activity       0.000000  0.000000  1.000000  1.00000   
injured_body_part                0.000000  0.000000  1.000000  1.00000   
injury_description               1.000000  0.000000  1.000000  0.00000   
VARIABLES => 75%                 3.000000  2.000000  5.000000  4.00000   
Cluster Value                    0.600000  0.400000  1.000000  0.80000   
Cluster adequate?                1.000000  0.000000  1.000000  1.00000   
Cluster percentage of accidents  4.081507  4.083566  3.609296  3.77614   
SCORE                                 NaN       NaN       NaN      NaN   

                                      12        13        14  \
VARIABLE                                                       
Quarter                          1.00000  1.000000  1.000000   
time_workday                     1.00000  1.000000  1.000000   
specific_physical_activity       0.00000  0.000000  1.000000   
injured_body_part                0.00000  0.000000  0.000000   
injury_description               1.00000  1.000000  0.000000   
VARIABLES => 75%                 3.00000  3.000000  3.000000   
Cluster Value                    0.60000  0.600000  0.600000   
Cluster adequate?                1.00000  1.000000  1.000000   
Cluster percentage of accidents  3.24574  1.950122  3.829695   
SCORE                                NaN       NaN       NaN   

                                 TOTAL CLUSTERIZATION VALUE  
VARIABLE                                                     
Quarter                                                 NaN  
time_workday                                            NaN  
specific_physical_activity                              NaN  
injured_body_part                                       NaN  
injury_description                                      NaN  
VARIABLES => 75%                                        NaN  
Cluster Value                                           NaN  